# Notebook 4: Compute d3 for testing facilities and residence centroids and visualize routes

## Introduction to Noteboook 4

In this notebook, we will:

1. compute `d3` using several methods
2. Obtain `d3_total` by adding `d1`, `d2` and `d3` from the selected method
3. Display residence centroids, testing facilities, a sample of 5 routes.

### Note

This notebook loads two graphs (projected and unprojected) and hence would consume a lot more memory. You should shut down other notebooks if you have memory constraints.

## Data sources

In [1]:
import pandas as pd, geopandas as gpd, folium, os

pd.options.display.float_format = '{:.10f}'.format

### Testing Facilities, Target Parish, Parishes, Residence Centroids

In [2]:
filtered_testing_sites_4326_gdf = gpd.read_file('data/filtered_testing_sites_4326_gdf.gpkg')
parish_gdf = gpd.read_file('data/parish_gdf.gpkg')
parishes_gdf = gpd.read_file('data/parishes_gdf.gpkg')
residential_centroids_4326_gdf = gpd.read_file('data/residential_centroids_4326_gdf.gpkg')

In [3]:
residential_centroids_4326_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 323 entries, 0 to 322
Data columns (total 14 columns):
 #   Column       Non-Null Count  Dtype   
---  ------       --------------  -----   
 0   parish_name  323 non-null    object  
 1   building     323 non-null    object  
 2   lat          323 non-null    float64 
 3   lon          323 non-null    float64 
 4   prj_lat      323 non-null    float64 
 5   prj_lon      323 non-null    float64 
 6   r_node       323 non-null    int64   
 7   d1           323 non-null    float64 
 8   r_node_lat   323 non-null    float64 
 9   r_node_lon   323 non-null    float64 
 10  r_node_x     323 non-null    float64 
 11  r_node_y     323 non-null    float64 
 12  d1_euc       323 non-null    float64 
 13  geometry     323 non-null    geometry
dtypes: float64(10), geometry(1), int64(1), object(2)
memory usage: 35.5+ KB


In [4]:
residential_centroids_4326_gdf.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [5]:
residential_centroids_4326_gdf

parish_name     building          lat           lon          prj_lat  \
0      Mutundwe        house 0.2859276891 32.5411339992 31604.6236591544   
1      Mutundwe        house 0.2889015267 32.5335200126 31933.3672625565   
2      Mutundwe  residential 0.2864849369 32.5472729671 31666.1911144829   
3      Mutundwe  residential 0.2865148305 32.5473939515 31669.4948266166   
4      Mutundwe  residential 0.2864484314 32.5473315974 31662.1557786760   
..          ...          ...          ...           ...              ...   
318    Mutundwe  residential 0.2877020718 32.5492533644 31800.7166323349   
319    Mutundwe  residential 0.2876436000 32.5491908000 31794.2538093184   
320    Mutundwe  residential 0.2877398000 32.5492090500 31804.8870535406   
321    Mutundwe  residential 0.2792401000 32.5358855500 30865.4430080952   
322    Mutundwe  residential 0.2792769624 32.5358344958 30869.5177662227   

              prj_lon      r_node            d1   r_node_lat    r_node_lon  \
0   448939.7847957994  2259657807 14.1625782501 0.2860422000 32.5410769000   
1   448092.5348129208  6224771050 21.7354518953 0.2887051000 32.5335109000   
2   449622.9139701424  7100593477 10.9136674412 0.2865830000 32.5472844000   
3   449636.3768886268  7100593469  4.6760845036 0.2865519000 32.5474142000   
4   449629.4380104926  7100593479 13.2613679893 0.2865676000 32.5473454000   
..                ...         ...           ...          ...           ...   
318 449843.2920636484  7108358940  4.3939560109 0.2877240000 32.5492863000   
319 449836.3298286514  7108359271  5.9883777345 0.2876952000 32.5491744000   
320 449838.3610546660  7108359271  6.2585685960 0.2876952000 32.5491744000   
321 448355.7224270308  7115878942 25.3789960856 0.2792195000 32.5361127000   
322 448350.0414099435  5519093504 18.5646249708 0.2793882000 32.5357095000   

             r_node_x         r_node_y        d1_euc                  geometry  
0   448933.4314661158 31617.2812191334 14.1625782501  POINT (32.54113 0.28593)  
1   448091.5198992379 31911.6555187456 21.7354518953  POINT (32.53352 0.28890)  
2   449624.1866144573 31677.0303263299 10.9136674412  POINT (32.54727 0.28648)  
3   449638.6302431334 31673.5921623061  4.6760845036  POINT (32.54739 0.28651)  
4   449630.9744488737 31675.3278414624 13.2613679893  POINT (32.54733 0.28645)  
..                ...              ...           ...                       ...  
318 449846.9571366845 31803.1402843450  4.3939560109  POINT (32.54925 0.28770)  
319 449834.5051105572 31799.9574109672  5.9883777345  POINT (32.54919 0.28764)  
320 449834.5051105572 31799.9574109672  6.2585685960  POINT (32.54921 0.28774)  
321 448380.9989812564 30863.1650158225 25.3789960856  POINT (32.53589 0.27924)  
322 448336.1327003257 30881.8138264484 18.5646249708  POINT (32.53583 0.27928)  

[323 rows x 14 columns]

In [6]:
filtered_testing_sites_4326_gdf.shape

(16, 17)

In [7]:
filtered_testing_sites_4326_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 16 entries, 0 to 15
Data columns (total 17 columns):
 #   Column       Non-Null Count  Dtype   
---  ------       --------------  -----   
 0   FACILITY     16 non-null     object  
 1   CITY         16 non-null     object  
 2   ADDRESS      16 non-null     object  
 3   LAT          16 non-null     float64 
 4   LON          16 non-null     float64 
 5   COORDINATES  16 non-null     object  
 6   NOTES        2 non-null      object  
 7   PRJ_LAT      16 non-null     float64 
 8   PRJ_LON      16 non-null     float64 
 9   t_node       16 non-null     int64   
 10  d2           16 non-null     float64 
 11  t_node_lat   16 non-null     float64 
 12  t_node_lon   16 non-null     float64 
 13  t_node_x     16 non-null     float64 
 14  t_node_y     16 non-null     float64 
 15  d2_euc       16 non-null     float64 
 16  geometry     16 non-null     geometry
dtypes: float64(10), geometry(1), int64(1), object(5)
memory usage: 2.2+

In [8]:
filtered_testing_sites_4326_gdf.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [9]:
filtered_testing_sites_4326_gdf

FACILITY     CITY  \
0          Central Public Health Laboratory  Kampala   
1   Infectious Disease Institute Laboratory  Kampala   
2                       Makerere University  Kampala   
3                       Mild May Laboratory  Kampala   
4     Joint Clinical Research Center (JCRC)  Kampala   
5                           MBN Laboroatory  Kampala   
6            Medipal International Hospital  Kampala   
7                   Test and Fly Laboratory  Kampala   
8                   Uganda Cancer Institute  Kampala   
9                            IOM Laboratory  Kampala   
10                             ANCA Biotech  Kampala   
11                              Case Clinic  Kampala   
12                MSF-Epicentre Lab-Mbarara  Kampala   
13                      Lancet Laboratories  Kampala   
14                        ATCG Laboratories  Kampala   
15                            Same Day Labs  Kampala   

                                              ADDRESS          LAT  \
0          7/11, Plot 113 Buganda Rd, Kampala, Uganda 0.3312460000   
1                      P.O.Box 22418, Kampala, Uganda 0.3391550000   
2                      University Rd, Kampala, Uganda 0.3337660000   
3                           6HG2+QJH, Kampala, Uganda 0.2272610000   
4                      P.o.Box 10005, Kampala, Uganda 0.2471060000   
5                Plot 28 Nakasero Rd, Kampala, Uganda 0.3244010000   
6           John Babiha (Acacia) Ave, Kampala, Uganda 0.3267710000   
7                    Yusuf Lule Road, Kampala, Uganda 0.3280000000   
8               Upper Mulago Hill Rd, Kampala, Uganda 0.3415660000   
9   Plot 6A Bukoto Crescent, Naguru, Kampala 11431... 0.3419140000   
10                   118 Luthuli Ave, Kampala, Uganda 0.3071250000   
11                  69-71 Buganda Rd, Kampala, Uganda 0.3249200000   
12  80, Plot 672, Hanlon Road, Nsambya Hill/P.O. B... 0.3007400000   
13              Plot 1 Kyadondo road, Kampala, Uganda 0.2883500000   
14  Plot M219 Nakawa Industrial Area, Inside UIRI,... 0.3378910000   
15  Office No 3, REGENCY PLAZA, 18 Lugogo By-Pass,... 0.3313330000   

             LON                              COORDINATES  \
0  32.5761710000     0.331245631028126, 32.57617147103373   
1  32.5761190000    0.3391550027171229, 32.57611913788221   
2  32.5675150000      0.33376643025242, 32.56751532874441   
3  32.5514940000  0.22726149143899727, 32.551493611083714   
4  32.5615450000   0.24710642516379605, 32.56154518525522   
5  32.5768040000    0.3244006304886406, 32.57680365762819   
6  32.5876990000   0.32677070175063294, 32.58769862875094   
7  32.5833240000    0.3279995303971809, 32.58332419987116   
8  32.5779390000  0.34156560138915515, 32.577938699857306   
9  32.6050250000     0.3419138946476636, 32.6050250521126   
10 32.6244090000   0.30712525960239967, 32.62440869986175   
11 32.5751340000   0.32492007311341675, 32.57513447097692   
12 32.5890170000  0.30073994493747824, 32.589017342090145   
13 32.5597390000    0.2883501600495953, 32.55973909986086   
14 32.6254010000   0.33789097348845115, 32.62540110209415   
15 32.6025240000    0.3313325589865815, 32.60252429988367   

                  NOTES          PRJ_LAT           PRJ_LON      t_node  \
0                  None 36613.6482006860 452838.7936172243  3799704477   
1                  None 37487.8549663987 452833.0450933628  7401202859   
2                  None 36892.2336127046 451875.5986544515  2297820937   
3                  None 25119.9449333336 450092.3882960156  2614743709   
4                  None 27313.4443953668 451210.9074285642  7062105534   
5                  None 35857.0460002950 452909.1994618282  6880975575   
6                  None 36118.9590743176 454121.5640353452  8193448456   
7                  None 36254.8242478438 453634.7367577547  7238684605   
8                  None 37754.3414306474 453035.5792187499  6232768975   
9                  None 37792.6787080598 456049.5983998349   560476404   
10                 None 33947.277966231

### Projected OSMNx graph for Kampala

In [10]:
import osmnx as ox, csv

with open('overpass-api.csv', mode='r') as infile:
    reader = csv.reader(infile)
    overpass_api = {rows[0]:rows[1] for rows in reader}

ox.config(
    log_console=False, 
    use_cache=True, 
    log_file=True,
    overpass_endpoint=overpass_api['main']
)

In [11]:
%%time
if 'G_proj' not in globals():
    G_proj = ox.load_graphml('data/g_projected.graphml')

if 'G' not in globals():
    G = ox.load_graphml('data/g_unprojected.graphml')

CPU times: user 40.2 s, sys: 1.19 s, total: 41.4 s
Wall time: 41.3 s


In [12]:
G_proj.graph['crs']

'+proj=utm +zone=36 +ellps=WGS84 +datum=WGS84 +units=m +no_defs +type=crs'

In [13]:
G.graph['crs']

'epsg:4326'

## Create residence-test facility pair DF and analysis columns

### D3 computation approaches

1. Method 1 (`d3_euc`) - Simple euclidean distance between closest node to a residence centroid and the closest node to a testing facility
2. Method 2 (`d3_path_sum`) - Sum of euclidean distances between nodes that constitute a path (same as Method 1 but euclidean distance is obtained for each node pair and then summed)
3. Method 3 (`d3_shapely`) - Total length of a Shapely LineString derived from list of coordinates that constitute a path
4. Method 4 (`d3_edge_attrs`) - Computed through OSMNx graph utils' route_edge_attributes function using "length" as weight

All methods, except Method 1, use the list of path nodes (path_node_list) generated from OSMNx shortest path function.

All methods, except Method 4, use a projected graph. 

References:

1. Method 1: https://osmnx.readthedocs.io/en/stable/osmnx.html#osmnx.distance.euclidean_dist_vec
2. Method 2: Same as Ref 1
3. Method 3: https://shapely.readthedocs.io/en/stable/manual.html
4. Method 4: https://github.com/gboeing/osmnx-examples/blob/main/notebooks/02-routing-speed-time.ipynb

### Create a Pandas DataFrame (`paired_df`) to store results of d1, d2, and d3 computation

Let's obtain a sample of residential units.

In [14]:
%%time
total_rows = 10
res_units_sample_gdf = residential_centroids_4326_gdf.sample(n=total_rows, random_state=1)

res_units_sample_gdf

CPU times: user 1.78 ms, sys: 65 µs, total: 1.84 ms
Wall time: 1.54 ms


parish_name     building          lat           lon          prj_lat  \
165    Mutundwe        house 0.2836238901 32.5451562390 31349.9586952977   
111    Mutundwe        house 0.2872418202 32.5452481555 31749.8610510506   
289    Mutundwe  residential 0.2860250976 32.5471301833 31615.3640677507   
223    Mutundwe        house 0.2799353250 32.5442204463 30942.2524388433   
73     Mutundwe        house 0.2858365797 32.5448846939 31594.5363920236   
256    Mutundwe        house 0.2783179634 32.5400988716 30763.4974547303   
174    Mutundwe        house 0.2847464038 32.5457406811 31474.0315934810   
249    Mutundwe        house 0.2787353357 32.5412247398 30809.6262564114   
150    Mutundwe        house 0.2852454684 32.5459370266 31529.1941152637   
260    Mutundwe  residential 0.2869269228 32.5488972538 31715.0382440446   

              prj_lon      r_node            d1   r_node_lat    r_node_lon  \
165 449387.3581206048  5568855301 14.6300492619 0.2835840000 32.5452816000   
111 449397.6021415021  6225526253  8.0291349359 0.2871910000 32.5451966000   
289 449607.0233894767  7103214804  4.6742574429 0.2860457000 32.5470935000   
223 449283.2098355863  6225392068 28.8820607025 0.2800148000 32.5444677000   
73  449357.1510122932  5508539562 26.9312406021 0.2857759000 32.5446503000   
256 448824.5654665851  6213151721 15.6487307896 0.2781923000 32.5400341000   
174 449452.3980492273  5573392203  7.9458428495 0.2848116000 32.5457106000   
249 448949.8507871045   557329612 31.2496795571 0.2787850000 32.5415012000   
150 449474.2489799075  5573150529 12.5231411346 0.2851617000 32.5460128000   
260 449803.6617480845  7108359045  4.4124536304 0.2869667000 32.5489006000   

             r_node_x         r_node_y        d1_euc                  geometry  
165 449401.3077629738 31345.5489539016 14.6300492619  POINT (32.54516 0.28362)  
111 449391.8649700851 31744.2439457506  8.0291349359  POINT (32.54525 0.28724)  
289 449602.9414741557 31617.6414895287  4.6742574429  POINT (32.54713 0.28603)  
223 449310.7238688410 30951.0360260652 28.8820607025  POINT (32.54422 0.27994)  
73  449331.0680703682 31587.8302857833 26.9312406021  POINT (32.54488 0.28584)  
256 448817.3573167607 30749.6076976614 15.6487307896  POINT (32.54010 0.27832)  
174 449449.0509899433 31481.2380914334  7.9458428495  POINT (32.54574 0.28475)  
249 448980.6147307725 30815.1146297963 31.2496795571  POINT (32.54122 0.27874)  
150 449482.6804596401 31519.9345681152 12.5231411346  POINT (32.54594 0.28525)  
260 449804.0342778018 31719.4349437898  4.4124536304  POINT (32.54890 0.28693)

### `paired_df`: Using `oxtools` functions

In [24]:
from oxtools.compute_d3 import create_paired_df, compute_d3

In [25]:
%%time
paired_df = create_paired_df(res_units_sample_gdf, filtered_testing_sites_4326_gdf)
paired_df = compute_d3(paired_df, G_proj, G)

CPU times: user 7.71 s, sys: 1.39 s, total: 9.1 s
Wall time: 44.1 s


### `paired_df`: Long way with more explanations (slower)

The earlier version of the code below is kept here in markdown format to explain what happens in the `oxtools` functions above.

```python
%%time
import networkx as nx, os
from tqdm import tqdm, notebook
from shapely.geometry import LineString


dict_list = []
df_list = []

# tqdm parameters
total_rows=5 #residential_centroids_4326_gdf.shape[0]

for r_index, r_row in tqdm(residential_centroids_4326_gdf.sample(n=total_rows, random_state=1).iterrows(), total=total_rows, desc='Residence Loop'):
    
    # for each sampled residence centroid, compute d3 and other parameters
    # create a dictionary for each pair and create a temporary DF for each dictionary
    dict_list = []
    for t_index, t_row in filtered_testing_sites_4326_gdf.iterrows():
        
        # 1. assemble the paired record using the nested loop
        r_parish_name = r_row['parish_name']
        r_node = r_row['r_node']
        r_node_lat = r_row['r_node_lat']
        r_node_lon = r_row['r_node_lon']
        t_node = t_row['t_node']
        t_node_lat = t_row['t_node_lat']
        t_node_lon = t_row['t_node_lon']
        d1 = r_row['d1']
        d2 = t_row['d2']
        
        # List if OSMNx nodes for shortest path
        path_node_list = ox.distance.shortest_path(G_proj, r_node, t_node, \
                                                   weight='length', cpus=2)

        ## d3 method 1 (sum of euclidean distance of path edges)
        # simplified explanation: 
        # 1. node to node distance: 
        #    osmnx.distance.euclidean_dist_vec(source_lat, source_lon, target_lat, 
        #        target_lon, distance)
        # 2. dist_list: list of node to node distances generated through Python list 
        #    comprehension (for loop)
        # 3. d3_path_sum: sum of distances in dist_list
        dist_list = [ ox.distance.euclidean_dist_vec(\
                    G_proj.nodes[path_node_list[i]]['y'], \
                    G_proj.nodes[path_node_list[i]]['x'], \
                    G_proj.nodes[path_node_list[i+1]]['y'], \
                    G_proj.nodes[path_node_list[i+1]]['x']) \
                    for i in range(len(path_node_list)-1) ]
        d3_path_sum = sum(dist_list)

        ## d3 method 2 (Shapely LineString Length)
        coords_list = [(G_proj.nodes[node]['x'], G_proj.nodes[node]['y']) \
                       for node in path_node_list ]
        path_line = LineString(coords_list)
        d3_shapely = path_line.length

        ## d3 method 3 (euclidean distance between residence centroid 
        #    and test facility coordinates
        d3_euc = ox.distance.euclidean_dist_vec(r_row['prj_lat'], r_row['prj_lon'], \
                                                t_row['PRJ_LAT'], t_row['PRJ_LON'])
        
        ## d3 method 4 (sum of lengths of edges through OSMNx edge attributes
        d3_edge_attrs = sum(ox.utils_graph.get_route_edge_attributes(G, \
                                  path_node_list, "length"))
        
        # obtain d_total
        d_total = d1 + d2 + d3_edge_attrs
        
        # assemble record dictionary
        record_dict = {
            'parish_name': r_parish_name,
            'r_node': r_node,
            'r_node_lat': r_node_lat,
            'r_node_lon': r_node_lon,
            't_node': t_node,
            't_node_lat': t_node_lat,
            't_node_lon': t_node_lon,
            'd3_euc': d3_euc,
            'd3_shapely': d3_shapely,
            'path_node_list': path_node_list,
            'path_distances': dist_list,
            'd3_path_sum': d3_path_sum,
            'd3_edge_attrs': d3_edge_attrs,
            'd_total': d_total
        }
        #print(record_dict)
        
        # append record dict to dict_list (each record is a future DF 
        #   row, each dict_list is future temp DF)
        dict_list.append(record_dict)
    
    # 2. Create a temporary DF to store list of record 
    #    dictionaries (these become DF rows)
    # Sort values by the d3_path_sum column
    # Group by r_node (remember each temp DF contains records for only one r_node)
    # Retain the first record (which would have the smallest value of d_total)
    df = pd.DataFrame(dict_list).sort_values(by=['d_total'])\
            .groupby(['r_node'], as_index=False).first()
    # append this temp DF to a DF list
    df_list.append(df)

# 3. Concatenate (combine) all the temp DFs in the DF list to a single DF
# Reset the index of the DF and drop the original indices of the temp DFs
paired_df = pd.concat(df_list).reset_index(drop=True)

# 4. Convert the path_node_list column to type string
paired_df['path_node_list'] = paired_df['path_node_list'].astype(str)

paired_df
```

In [26]:
paired_df

r_node parish_name   r_node_lat    r_node_lon          prj_lat  \
0   557329612    Mutundwe 0.2787850000 32.5415012000 30809.6262564114   
1  5508539562    Mutundwe 0.2857759000 32.5446503000 31594.5363920236   
2  5568855301    Mutundwe 0.2835840000 32.5452816000 31349.9586952977   
3  5573150529    Mutundwe 0.2851617000 32.5460128000 31529.1941152637   
4  5573392203    Mutundwe 0.2848116000 32.5457106000 31474.0315934810   
5  6213151721    Mutundwe 0.2781923000 32.5400341000 30763.4974547303   
6  6225392068    Mutundwe 0.2800148000 32.5444677000 30942.2524388433   
7  6225526253    Mutundwe 0.2871910000 32.5451966000 31749.8610510506   
8  7103214804    Mutundwe 0.2860457000 32.5470935000 31615.3640677507   
9  7108359045    Mutundwe 0.2869667000 32.5489006000 31715.0382440446   

            prj_lon      t_node   t_node_lat    t_node_lon          PRJ_LAT  \
0 448949.8507871045  5572008964 0.2883498000 32.5594612000 31872.2887513557   
1 449357.1510122932  5572008964 0.2883498000 32.5594612000 31872.2887513557   
2 449387.3581206048  5572008964 0.2883498000 32.5594612000 31872.2887513557   
3 449474.2489799075  5572008964 0.2883498000 32.5594612000 31872.2887513557   
4 449452.3980492273  5572008964 0.2883498000 32.5594612000 31872.2887513557   
5 448824.5654665851  5572008964 0.2883498000 32.5594612000 31872.2887513557   
6 449283.2098355863  5572008964 0.2883498000 32.5594612000 31872.2887513557   
7 449397.6021415021  5572008964 0.2883498000 32.5594612000 31872.2887513557   
8 449607.0233894767  5572008964 0.2883498000 32.5594612000 31872.2887513557   
9 449803.6617480845  5572008964 0.2883498000 32.5594612000 31872.2887513557   

            PRJ_LON            d1            d2  \
0 451010.1044428619 31.2496795571 30.9127230872   
1 451010.1044428619 26.9312406021 30.9127230872   
2 451010.1044428619 14.6300492619 30.9127230872   
3 451010.1044428619 12.5231411346 30.9127230872   
4 451010.1044428619  7.9458428495 30.9127230872   
5 451010.1044428619 15.6487307896 30.9127230872   
6 451010.1044428619 28.8820607025 30.9127230872   
7 451010.1044428619  8.0291349359 30.9127230872   
8 451010.1044428619  4.6742574429 30.9127230872   
9 451010.1044428619  4.4124536304 30.9127230872   

                                      path_node_list          d3_euc  \
0  [557329612, 6219148347, 557329299, 557329297, ... 2318.1666687758   
1  [5508539562, 6227614261, 5508539561, 550853956... 1676.1269094981   
2  [5568855301, 5568855300, 5573392591, 557339224... 1704.7387817084   
3  [5573150529, 5573150528, 5573150527, 557315052... 1573.7108795462   
4  [5573392203, 5573392202, 5573392201, 557339220... 1607.8115475915   
5  [6213151721, 6213151722, 6213151723, 809625964... 2450.7139278784   
6  [6225392068, 6225392069, 6225392070, 557315093... 1961.4108512061   
7  [6225526253, 6226887750, 1242682715, 557345641... 1617.1432260912   
8  [7103214804, 7105675803, 7105675698, 557314191... 1426.4104372214   
9  [7108359045, 7108359027, 7108359026, 710835899... 1216.6477295550   

      d3_path_sum                                         d3_shapely  \
0 3032.5987039978  LINESTRING (448980.6147307725 30815.1146297963...   
1 2299.2602558018  LINESTRING (449331.0680703682 31587.8302857833...   
2 2181.2087256605  LINESTRING (449401.3077629738 31345.5489539015...   
3 2018.3940642422  LINESTRING (449482.6804596401 31519.9345681151...   
4 2050.0275152189  LINESTRING (449449.0509899433 31481.2380914333...   
5 3212.6984562085  LINESTRING (448817.3573167607 30749.6076976613...   
6 2545.3698038693  LINESTRING (449310.72386884096 30951.036026065...   
7 2079.9942224742  LINESTRING (449391.8649700851 31744.2439457506...   
8 1862.4199218747  LINESTRING (449602.9414741557 31617.6414895286...   
9 1621.7886580908  LINESTRING (449804.03427780175 31719.434943789...   

    d3_edge_attrs         d_total  
0 3037.3600000000 3099.5224026443  
1 2302.1450000000 2359.9889636893  
2 2184.3380000000 2229.8807723491  
3 2020.9530000000 2064.3888642218  
4 205

## Map Paired Residence Centroids and Test Facilities and Node-to-Node Routes

In [27]:
%%time
import folium, json
from folium import plugins

map1 = filtered_testing_sites_4326_gdf.explore(marker_kwds=dict(radius=5))

# Tile Layer (can add more, these become radio buttons on Layer Control)
folium.TileLayer('cartodbpositron').add_to(map1)
folium.TileLayer('cartodbdark_matter').add_to(map1)

# Feature groups become checkboxes in Layer Control Widget
fg1=folium.FeatureGroup(name='Residences', show=True)
fg2=folium.FeatureGroup(name='Residence Nodes', show=True)
fg3=folium.FeatureGroup(name='Residence to Node', show=True)

# Residences, Nodes and Residence-to-Node Paths
for row in residential_centroids_4326_gdf.itertuples():

    folium.CircleMarker(
                    location=[row.lat,row.lon], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='red', \
                    fill_opacity=1).add_to(fg1)


    folium.CircleMarker(
                    location=[row.r_node_lat,row.r_node_lon], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='yellow', \
                    fill_opacity=1).add_to(fg2)
    
    r_line_points = ((row.lat,row.lon),(row.r_node_lat,row.r_node_lon))
    popup_d1 = folium.Popup('d1: '+str(row.d1)+' meters')
    folium.PolyLine(r_line_points,
                    color='gray',
                    popup=popup_d1,
                    weight=2,
                    opacity=0.8
                   ).add_to(fg3)

fg1.add_to(map1)
fg2.add_to(map1)
fg3.add_to(map1)

# Residences, Nodes and Residence-to-Node Paths
fg4=folium.FeatureGroup(name='Testing Sites', show=True)
fg5=folium.FeatureGroup(name='Testing Site Nodes', show=True)
fg6=folium.FeatureGroup(name='Testing Site to Node', show=True)

for row in filtered_testing_sites_4326_gdf.itertuples():

    folium.CircleMarker(
                    location=[row.LAT,row.LON], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='blue', \
                    fill_opacity=1).add_to(fg4)


    folium.CircleMarker(
                    location=[row.t_node_lat,row.t_node_lon], \
                    radius=4, \
                    color='black', \
                    weight=1, \
                    fill=True, \
                    fill_color='yellow', \
                    fill_opacity=1).add_to(fg5)
    
    t_line_points = ((row.LAT,row.LON),(row.t_node_lat,row.t_node_lon))
    popup_d2 = folium.Popup('d2: '+str(row.d2)+' meters')
    folium.PolyLine(t_line_points,
                    color='gray',
                    popup=popup_d2,
                    weight=2,
                    opacity=0.8
                   ).add_to(fg6)
fg4.add_to(map1)
fg5.add_to(map1)
fg6.add_to(map1)

# Node to Node Routes
fg7=folium.FeatureGroup(name='Node to Node Routes', show=True)
for row in paired_df.itertuples():
    #path_string = row['path_node_list']
    #path_node_list = json.loads(path_string)
    edge_list = []
    #path_node_list = row.path_node_list
    path_node_list = [ int(item.strip()) for item in str(row.path_node_list).strip('[]').split(',') ]
    for i in range(len(path_node_list)-1):
        edge_pair = ((G_proj.nodes[path_node_list[i]]['lat'], G_proj.nodes[path_node_list[i]]['lon']), \
                     (G_proj.nodes[path_node_list[i+1]]['lat'], G_proj.nodes[path_node_list[i+1]]['lon']))
        edge_list.append(edge_pair)
        popup = folium.Popup('d_total: '+str(row.d_total/1000)+' km')
        folium.PolyLine(edge_list,
                        color='red',
                        weight=2,
                        opacity=0.8,
                        popup=popup
                       ).add_to(fg7)
fg7.add_to(map1)

# GeoJSON parish boundary with style function
fg8=folium.FeatureGroup(name='Parish Boundary', show=True)
parish_name = ''.join(paired_df['parish_name'].unique())
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0, 
                            'weight': 3}
geojson = folium.GeoJson(
    data=parish_gdf['geometry'], 
    name="geojson",
    style_function=style_function
)
geojson.add_child(folium.Popup('Parish Boundary: '+parish_name))
geojson.add_to(fg8)
fg8.add_to(map1)

# Let's give the user the option to turn this feature group on (set it to False).
#  This feature group overlaps with feature group 8.
fg9=folium.FeatureGroup(name='Parishes', show=False)
for r in parishes_gdf.itertuples():
    # Simplify the representation of the parishes
    #    so the polygons display easily
    sim_geo = gpd.GeoSeries(r.geometry).simplify(tolerance=0.00001)
    # convert the simplified geometry to GeoJSON
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'color':'black','weight':2, 'fillColor': 'orange','fillOpacity':0.05},
                           highlight_function=lambda x: {'color':'black','weight':2, 'fillColor': 'blue','fillOpacity':0.075})
    # prepare the popup for each parish (name and area in sq m)
    folium.Popup('Parish: '+r.NAME_4+'<br/>'+'Area (sq. m.): '+str(r.area_sqm)).add_to(geo_j)
    geo_j.add_to(fg9)
fg9.add_to(map1)

# The following are map controls:
# 1. Layer Control
folium.LayerControl(position='topright', collapsed=True, autoZIndex=True).add_to(map1)
# 2. Measure Control
map1.add_child(plugins.MeasureControl(activecolor = "blue", completedcolor = "black",))
# 3. Full Screen button
plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(map1)

map1

CPU times: user 618 ms, sys: 20.1 ms, total: 638 ms
Wall time: 637 ms


## Housekeeping

In [28]:
paired_df.to_pickle('data/paired_df.pickle')

In [29]:
if os.path.exists('data/paired_cache_df.pickle'):
    paired_cache_df = pd.read_pickle('data/paired_cache_df.pickle')
else:
    paired_cache_df = pd.DataFrame()

if (paired_cache_df.empty) or (parish_name not in paired_cache_df['parish_name'].values):
    paired_cache_df = paired_cache_df.append(paired_df, ignore_index=True)
    paired_cache_df.to_pickle('data/paired_cache_df.pickle')

paired_cache_df['parish_name'].unique()

array(['Kabowa', 'Kisugu', 'Kawempe I', 'Bogolobi', 'Bwaise I', 'Ggaba',
       'Nakulabye', 'Luwafu', 'Busega', 'Kasubi', 'Mutundwe'],
      dtype=object)